### Urlfr_tgt_cnt calculation

In [1]:
code = '''
import datetime
from datetime import date, timedelta
import sys

print('{0}: prod_features_liveinternet.urlfr_tgt_cnt update started').format(datetime.datetime.now())

HIVE_HOST = 'ds-hadoop-cs01p'
HIVE_PORT = 10000
HIVE_USER = 'bigdatasys'
CONF={'hive.vectorized.execution.enabled':'true'
    ,'mapreduce.map.memory.mb':'4096'
    ,'mapreduce.map.child.java.opts':'-Xmx4g'
    ,'mapreduce.task.io.sort.mb':'1024'
    ,'mapreduce.reduce.child.java.opts':'-Xmx4g'
    ,'mapreduce.reduce.memory.mb':'7000'
    ,'mapreduce.reduce.shuffle.input.buffer.percent':'0.5'
    ,'mapreduce.input.fileinputformat.split.minsize':'536870912'
    ,'mapreduce.input.fileinputformat.split.maxsize':'1073741824'
    ,'hive.optimize.ppd':'true'
    ,'hive.merge.smallfiles.avgsize':'536870912'
    ,'hive.merge.mapredfiles':'true'
    ,'hive.merge.mapfiles':'true'
    ,'hive.hadoop.supports.splittable.combineinputformat':'true'
    ,'hive.exec.reducers.bytes.per.reducer':'536870912'
    ,'hive.exec.parallel':'true'
    ,'hive.exec.max.created.files':'10000000'
    ,'hive.exec.compress.output':'true'
    ,'hive.exec.dynamic.partition.mode':'nonstrict'
    ,'hive.exec.max.dynamic.partitions':'1000000'
    ,'hive.exec.max.dynamic.partitions.pernode':'100000'
    ,'io.seqfile.compression.type':'BLOCK'
    ,'mapreduce.map.failures.maxpercent':'5'
          }

from pyhive import hive
conn = hive.Connection(host=HIVE_HOST, port=HIVE_PORT, username=HIVE_USER, configuration=CONF)
cursor = conn.cursor()

ymd_to_process = datetime.datetime.strptime(sys.argv[1],'%Y-%m-%d')

action_type_to_load = ['tinkoff_platinum_complete_application', 'tinkoff_platinum_approved_application']

query_pattern = \'\'\'
WITH t AS 
 (
   SELECT
   v.url_fragment AS urlfr
   ,COUNT(*) AS cnt_positive   
  FROM
   (SELECT DISTINCT a.id FROM prod_features_liveinternet.user_action a WHERE a.ymd between '#ymd_start' and '#ymd_end' and a.action_type = '#action_type') ta 
    inner join prod_odd.visit_feature v on v.id = ta.id    
  WHERE
   v.ymd='#ymd0' 
   and v.load_src = "LI.02"
  GROUP BY 
   v.url_fragment
   ) 
  
INSERT OVERWRITE TABLE 
 prod_features_liveinternet.urlfr_tgt_cnt PARTITION (ymd='#ymd0', target='#action_type#N@tinkoff_action') 
SELECT 
 s.urlfr AS urlfr
 ,nvl(t.cnt_positive, 0) as cnt_positive
 ,s.visitors as cnt_total
 ,current_timestamp() as load_dttm
FROM
 prod_features_liveinternet.urlfr_stat s 
 LEFT OUTER JOIN t ON t.urlfr = s.urlfr 
WHERE 
 s.ymd='#ymd0'
\'\'\'

for at in action_type_to_load:
    if True:
        #ymd_to_process = datetime.date.today() - datetime.timedelta(days = 4)
        ymd0      = ymd_to_process.strftime('%Y-%m-%d')
        ymd_start = (ymd_to_process + datetime.timedelta(days = 0)).strftime('%Y-%m-%d')
        ymd_end   = (ymd_to_process + datetime.timedelta(days = 3)).strftime('%Y-%m-%d')
        N = '03'
    q = query_pattern.replace('#action_type', at).replace('#ymd0',ymd0).replace('#ymd_start',ymd_start).replace('#ymd_end',ymd_end).replace('#N', N)
    #print(q)
    cursor.execute(q)

print('{0}: prod_features_liveinternet.urlfr_tgt_cnt successfully updated. Date: {1}').format(datetime.datetime.now(),ymd_to_process)
'''


In [2]:
import datetime
open('./scripts/urlfr_tgt_cnt.py','w').write(code)
#dates_to_calc = ([datetime.datetime(2016,12,1) + datetime.timedelta(days=i) for i in range(31*2)] +
#                 [datetime.datetime(2017,4,1) + datetime.timedelta(days=i) for i in range(31)]                 
#                )
dates_to_calc = ([datetime.datetime(2017,5,20) + datetime.timedelta(days=i) for i in range(31)]              
                )

open('./data/urlfr_tgt_cnt_dates_to_calc.txt','w').write('\n'.join([d.strftime('%Y-%m-%d') for d in dates_to_calc]))



In [3]:
#Execute
#! cat ./data/urlfr_tgt_cnt_dates_to_calc.txt | xargs -P 4 -I '{}' sh -c 'echo {}'
! cat ./data/urlfr_tgt_cnt_dates_to_calc.txt |  xargs -P 8 -I '{}' sh -c '/opt/anaconda/bin/python ./scripts/urlfr_tgt_cnt.py {} >> ./data/urlfr_tgt_cnt.log'

### Another approach

In [38]:
code1 = '''
set hive.vectorized.execution.enabled=true;
set mapreduce.map.memory.mb=4096;
set mapreduce.map.child.java.opts=-Xmx4g;
set mapreduce.task.io.sort.mb=1024;
set mapreduce.reduce.child.java.opts=-Xmx4g;
set mapreduce.reduce.memory.mb=4096;
set mapreduce.reduce.shuffle.input.buffer.percent=0.5;
set mapreduce.input.fileinputformat.split.minsize=268435456;
set mapreduce.input.fileinputformat.split.maxsize=536870912;
set hive.optimize.ppd=true;
set hive.merge.smallfiles.avgsize=268435456;
set hive.merge.mapredfiles=true;
set hive.merge.mapfiles=true;
set hive.hadoop.supports.splittable.combineinputformat=true;
set hive.exec.reducers.bytes.per.reducer=268435456;
set hive.exec.parallel=true;
set hive.exec.max.created.files=100000000;
set hive.exec.compress.output=true;
set hive.exec.dynamic.partition.mode=nonstrict;
set hive.exec.max.dynamic.partitions=10000000;
set hive.exec.max.dynamic.partitions.pernode=1000000;
set io.seqfile.compression.type=BLOCK;
set mapred.output.compression.codec=org.apache.hadoop.io.compress.BZip2Codec;
set mapreduce.map.failures.maxpercent=5;
set hive.tez.auto.reducer.parallelism=true;
set hive.tez.min.partition.factor=0.25;
set hive.tez.max.partition.factor=2.0;
set tez.runtime.pipelined.sorter.lazy-allocate.memory=true;
set mapreduce.map.output.compress=true;
set mapreduce.map.output.compress.codec=org.apache.hadoop.io.compress.SnappyCodec;

set CALC_LAST_DATE;

CREATE
 TABLE if not exists prod_features_liveinternet.url_fragment_target_cnt 
     (`url_fragment` string, 
	  `cnt_total` bigint, 
	  `cnt_positive` map<string,int>, 
	  `score` map<string,double>, 
	  `load_dttm` timestamp
     ) PARTITIONED BY 
     (ymd string)
STORED
    AS RCFile
    ;

with t as (

select url_fragment
     , count(distinct positive_tpca) as cnt_positive_tpca
     , count(distinct positive_tpaa) as cnt_positive_tpaa
     , count(distinct positive_aaca) as cnt_positive_aaca
     , count(distinct positive_aaaa) as cnt_positive_aaaa
     , count(distinct id) as cnt_total
     , "${hiveconf:CALC_LAST_DATE}" as ymd
  from(select vf.id
            , vf.url_fragment
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'tinkoff_platinum_complete_application' then ua.id end
           as positive_tpca
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'tinkoff_platinum_approved_application' then ua.id end
           as positive_tpaa
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'all_airlines_complete_application' then ua.id end
           as positive_aaca
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'all_airlines_approved_application' then ua.id end
           as positive_aaaa
         from prod_odd.visit_feature vf
         left 
         join (select distinct 
                      id
                    , action_type  
                    , ymd 
                 from prod_odd.user_action
                where ymd between "${hiveconf:CALC_LAST_DATE}" and date_add("${hiveconf:CALC_LAST_DATE}",3)
                  and action_type in ('tinkoff_platinum_complete_application', 'tinkoff_platinum_approved_application', 'all_airlines_complete_application', 'all_airlines_approved_application')
               ) ua on ua.id = vf.id
        where vf.ymd = "${hiveconf:CALC_LAST_DATE}"
          and trim(vf.url_fragment) != '#'
          and vf.load_src = 'LI.02'
        ) k
 group
    by url_fragment
 having (cnt_total > 500 or cnt_positive_tpca + cnt_positive_tpaa + cnt_positive_aaca + cnt_positive_aaaa > 0)
)

insert overwrite
table prod_features_liveinternet.url_fragment_target_cnt partition ( ymd )
select url_fragment
     , cnt_total
     , map('tinkoff_platinum_complete_application03_1m', cast(coalesce(cnt_positive_tpca, 0) as int),
           'tinkoff_platinum_approved_application03_1m', cast(coalesce(cnt_positive_tpaa, 0) as int),
           'all_airlines_complete_application03_1m', cast(coalesce(cnt_positive_aaca, 0) as int),
           'all_airlines_approved_application03_1m', cast(coalesce(cnt_positive_aaaa, 0) as int)
           ) as cnt_positive
     , map('tinkoff_platinum_complete_application03_1m', log((cnt_positive_tpca + 0.1) / (cnt_total - cnt_positive_tpca + 0.1)),
           'tinkoff_platinum_approved_application03_1m', log((cnt_positive_tpaa + 0.1) / (cnt_total - cnt_positive_tpaa + 0.1)),
           'all_airlines_complete_application03_1m', log((cnt_positive_aaca + 0.1) / (cnt_total - cnt_positive_aaca + 0.1)),
           'all_airlines_approved_application03_1m', log((cnt_positive_aaaa + 0.1) / (cnt_total - cnt_positive_aaaa + 0.1))
           ) as score
     , current_timestamp as load_dttm
     , "${hiveconf:CALC_LAST_DATE}" as ymd
  from t
; 
'''

In [39]:
import datetime
open('./scripts/urlfr_tgt_cnt_calc.sql','w').write(code1)
dates_to_calc = ([datetime.datetime(2017,7,24) + datetime.timedelta(days=-i) for i in range(121)]
                )
open('./data/urlfr_tgt_cnt_dates_to_calc.txt','w').write('\n'.join([d.strftime('%Y-%m-%d') for d in dates_to_calc]))

In [ ]:
#Execute
! cat ./data/urlfr_tgt_cnt_dates_to_calc.txt |  xargs -P 8 -I '{}' sh -c 'beeline -u "jdbc:hive2://ds-hadoop-cs01p:10000/" -n kposminin -hiveconf  CALC_LAST_DATE="{}" -f ./scripts/urlfr_tgt_cnt_calc.sql 2>&1 > ./scripts/urlfr_tgt_cnt_calc.log'


ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
ls: cannot access /home/k.p.osminin/spark-2.1.1-bin-hadoop2.6/lib/spark-assembly-*.jar: No such file or directory
OpenJDK 64-Bit Server VM warning: ignoring option MaxPermSize=512M; support was removed 

In [9]:
code2 = '''
import datetime
from datetime import date, timedelta
import sys

ymd_to_process = datetime.datetime.strptime(sys.argv[1],'%Y-%m-%d')

print('{0}: prod_features_liveinternet.urlfr_tgt_cnt update started for {1}.'.format(datetime.datetime.now(),ymd_to_process))

HIVE_HOST = 'ds-hadoop-cs01p'
HIVE_PORT = 10000
HIVE_USER = 'bigdatasys'
CONF={'hive.vectorized.execution.enabled':'true'
    ,'mapreduce.map.memory.mb':'4096'
    ,'mapreduce.map.child.java.opts':'-Xmx4g'
    ,'mapreduce.task.io.sort.mb':'1024'
    ,'mapreduce.reduce.child.java.opts':'-Xmx4g'
    ,'mapreduce.reduce.memory.mb':'7000'
    ,'mapreduce.reduce.shuffle.input.buffer.percent':'0.5'
    ,'mapreduce.input.fileinputformat.split.minsize':'536870912'
    ,'mapreduce.input.fileinputformat.split.maxsize':'1073741824'
    ,'hive.optimize.ppd':'true'
    ,'hive.merge.smallfiles.avgsize':'536870912'
    ,'hive.merge.mapredfiles':'true'
    ,'hive.merge.mapfiles':'true'
    ,'hive.hadoop.supports.splittable.combineinputformat':'true'
    ,'hive.exec.reducers.bytes.per.reducer':'536870912'
    ,'hive.exec.parallel':'true'
    ,'hive.exec.max.created.files':'10000000'
    ,'hive.exec.compress.output':'true'
    ,'hive.exec.dynamic.partition.mode':'nonstrict'
    ,'hive.exec.max.dynamic.partitions':'1000000'
    ,'hive.exec.max.dynamic.partitions.pernode':'100000'
    ,'io.seqfile.compression.type':'BLOCK'
    ,'mapreduce.map.failures.maxpercent':'5'
          }

from pyhive import hive
conn = hive.Connection(host=HIVE_HOST, port=HIVE_PORT, username=HIVE_USER, configuration=CONF)
cursor = conn.cursor()
init_query = \'\'\'
CREATE
 TABLE if not exists prod_features_liveinternet.url_fragment_target_cnt 
     (`url_fragment` string, 
	  `cnt_total` bigint, 
	  `cnt_positive` map<string,int>, 
	  `score` map<string,double>, 
	  `load_dttm` timestamp
     ) PARTITIONED BY 
     (ymd string)
STORED
    AS RCFile
    ;
\'\'\'

query_pattern = \'\'\'

with t as (

select url_fragment
     , count(distinct positive_tpca) as cnt_positive_tpca
     , count(distinct positive_tpaa) as cnt_positive_tpaa
     , count(distinct positive_aaca) as cnt_positive_aaca
     , count(distinct positive_aaaa) as cnt_positive_aaaa
     , count(distinct id) as cnt_total
     , "#ymd0" as ymd
  from(select vf.id
            , vf.url_fragment
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'tinkoff_platinum_complete_application' then ua.id end
           as positive_tpca
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'tinkoff_platinum_approved_application' then ua.id end
           as positive_tpaa
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'all_airlines_complete_application' then ua.id end
           as positive_aaca
            , case when ua.ymd between vf.ymd and date_add(vf.ymd, 3) and ua.action_type = 'all_airlines_approved_application' then ua.id end
           as positive_aaaa
         from prod_odd.visit_feature vf
         left 
         join (select distinct 
                      id
                    , action_type  
                    , ymd 
                 from prod_odd.user_action
                where ymd between "#ymd0" and date_add("#ymd0",3)
                  and action_type in ('tinkoff_platinum_complete_application', 'tinkoff_platinum_approved_application', 'all_airlines_complete_application', 'all_airlines_approved_application')
               ) ua on ua.id = vf.id
        where vf.ymd = "#ymd0"
          and trim(vf.url_fragment) != '#'
          and vf.load_src = 'LI.02'
        ) k
 group
    by url_fragment
 having (cnt_total > 500 or cnt_positive_tpca + cnt_positive_tpaa + cnt_positive_aaca + cnt_positive_aaaa > 0)
)

insert overwrite
table prod_features_liveinternet.url_fragment_target_cnt partition ( ymd )
select url_fragment
     , cnt_total
     , map('tinkoff_platinum_complete_application03_1m', cast(coalesce(cnt_positive_tpca, 0) as int),
           'tinkoff_platinum_approved_application03_1m', cast(coalesce(cnt_positive_tpaa, 0) as int),
           'all_airlines_complete_application03_1m', cast(coalesce(cnt_positive_aaca, 0) as int),
           'all_airlines_approved_application03_1m', cast(coalesce(cnt_positive_aaaa, 0) as int)
           ) as cnt_positive
     , map('tinkoff_platinum_complete_application03_1m', log((cnt_positive_tpca + 0.1) / (cnt_total - cnt_positive_tpca + 0.1)),
           'tinkoff_platinum_approved_application03_1m', log((cnt_positive_tpaa + 0.1) / (cnt_total - cnt_positive_tpaa + 0.1)),
           'all_airlines_complete_application03_1m', log((cnt_positive_aaca + 0.1) / (cnt_total - cnt_positive_aaca + 0.1)),
           'all_airlines_approved_application03_1m', log((cnt_positive_aaaa + 0.1) / (cnt_total - cnt_positive_aaaa + 0.1))
           ) as score
     , current_timestamp as load_dttm
     , "#ymd0" as ymd
  from t

\'\'\'


ymd0      = ymd_to_process.strftime('%Y-%m-%d')
ymd_start = (ymd_to_process + datetime.timedelta(days = 0)).strftime('%Y-%m-%d')
ymd_end   = (ymd_to_process + datetime.timedelta(days = 3)).strftime('%Y-%m-%d')
N = '03'
q = query_pattern.replace('#ymd0',ymd0).replace('#ymd_start',ymd_start).replace('#ymd_end',ymd_end)
#print(q)
cursor.execute(q)

print('{0}: prod_features_liveinternet.urlfr_tgt_cnt successfully updated. Date: {1}').format(datetime.datetime.now(),ymd_to_process)
'''


In [10]:
import datetime
open('./scripts/urlfr_tgt_cnt.py','w').write(code2)
#dates_to_calc = ([datetime.datetime(2016,12,1) + datetime.timedelta(days=i) for i in range(31*2)] +
#                 [datetime.datetime(2017,4,1) + datetime.timedelta(days=i) for i in range(31)]                 
#                )
dates_to_calc = ([datetime.datetime(2017,7,24) - datetime.timedelta(days=i) for i in range(121)]              
                )

open('./data/urlfr_tgt_cnt_dates_to_calc.txt','w').write('\n'.join([d.strftime('%Y-%m-%d') for d in dates_to_calc]))


In [11]:
#Execute
! cat ./data/urlfr_tgt_cnt_dates_to_calc.txt |  xargs -P 8 -I '{}' sh -c '/opt/anaconda/bin/python ./scripts/urlfr_tgt_cnt.py {} >> ./data/urlfr_tgt_cnt.log'

### Аккумуляция за месяц

In [ ]:
monthly_cumul_query = '''
  with tmp as (
    select
           url_fragment, 
           sum(cnt_total) as cnt_total, 
           map('tinkoff_platinum_complete_application03_1m', cast(sum(cnt_positive['tinkoff_platinum_complete_application03_1m']) as int),
               'tinkoff_platinum_approved_application03_1m',  cast(sum(cnt_positive['tinkoff_platinum_approved_application03_1m']) as int),
               'all_airlines_complete_application03_1m',      cast(sum(cnt_positive['all_airlines_complete_application03_1m']) as int),
               'all_airlines_approved_application03_1m',      cast(sum(cnt_positive['all_airlines_approved_application03_1m']) as int)
           ) as cnt_positive
      from prod_features_liveinternet.url_fragment_target_cnt
     where ymd between date_add('#ymd0',-30) and '#ymd0'
     group by url_fragment
     )
insert overwrite table prod_features_liveinternet.url_fragment_target_cnt_cumulative partition (period,ymd)
select url_fragment, 
       cnt_total, 
       cnt_positive, 
       map('tinkoff_platinum_complete_application03_1m', log((cnt_positive['tinkoff_platinum_complete_application03_1m'] + 0.1) / 
                                                             (cnt_total - cnt_positive['tinkoff_platinum_complete_application03_1m'] + 0.1)),
           'tinkoff_platinum_approved_application03_1m', log((cnt_positive['tinkoff_platinum_approved_application03_1m'] + 0.1) / 
                                                             (cnt_total - cnt_positive['tinkoff_platinum_approved_application03_1m'] + 0.1)),
           'all_airlines_complete_application03_1m', log((cnt_positive['all_airlines_complete_application03_1m'] + 0.1) / 
                                                             (cnt_total - cnt_positive['all_airlines_complete_application03_1m'] + 0.1)),
           'all_airlines_approved_application03_1m', log((cnt_positive['all_airlines_approved_application03_1m'] + 0.1) / 
                                                             (cnt_total - cnt_positive['all_airlines_approved_application03_1m'] + 0.1))
           ) as score,
       current_timestamp as load_dttm,
       30 as period,
       '#ymd0' as ymd
  from tmp
'''

 